# CORESE client: query

CORESE is a Semantic Web Factory (triple store & SPARQL endpoint) implementing RDF, RDFS, SPARQL 1.1 Query & Update. This notebook is intended to be used as a test client for the local CORESE server.

For more information see: https://project.inria.fr/corese

In [1]:
from __future__ import print_function

## Setup and run CORESE server

### Download CORESE server 

Download the server from https://project.inria.fr/corese/download/

Only do it once. 

### Modify the profile.ttl file

1. Define a profile.ttl document as shown in the downloaded profile.ttl file.
The string "myserver" is the name of the service that you implement, you can choose another name. 
Put profile.ttl in a directory (say absolute path DIR) in your file system.

2. Specify the file(s) that you want to load
in your service by setting, in profile.ttl,  the value of the sw:path property. In the example, replace  <http://www.w3.org/1999/02/22-rdf-syntax-ns> by the URL of your document. It can be a path in the file system.  The path can be relative to the path of profile.ttl. URL and path must be within "<" and ">".
If you load several documents, write the list of URL/path separated by comma "," :
sw:path <u1>, <u2>, ... 
The profile.ttl document is  RDF in Turtle syntax.
    
One time operation

### Start the server

Run the following command from the directory where the server is downloaded

_java -jar -Dfile.encoding=UTF8 -Xmx20G corese-server-4.1.2.jar -e -lp -debug -pp profile.ttl_

or if running on Windows change the path and run the code below.

NOTE: please notice that the server name/version in the command line should corresponds to your server executable.

In [ ]:
import os
import subprocess

corese_path = os.path.normpath('C:/Users/abobashe/Documents/MonaLIA/CORESE')
command_line = 'start /w cmd /k java -jar -Dfile.encoding=UTF8 -Xmx20G corese-server-4.1.2.jar -e -lp -debug -pp profile.ttl'

corese_server = subprocess.Popen(command_line, shell=True, cwd=corese_path)

## Install SPARQLWrapper package

This package helps to convert service output to a Pandas DataFrame. https://rdflib.dev/sparqlwrapper/

NOTE: If you are running Anaconda distribution and prefer the conda installation find the command here https://anaconda.org/conda-forge/sparqlwrapper

Only run it once or periodically to check for the updates.

In [ ]:
!pip install SPARQLWrapper

In [2]:
import SPARQLWrapper
import json
print('SPARQLWrapper ver.', SPARQLWrapper.__version__)

from SPARQLWrapper import SPARQLWrapper, JSON, XML

SPARQLWrapper ver. 1.8.5


## Install Pandas package

To use Pandas DataFrame to contain the query results.

NOTE: if you are running Anaconda distribution the preferred way to install pandas is:

_conda install pandas_

Only run it once or periodically to check for the updates.

In [ ]:
!pip install pandas

In [3]:
import pandas as pd
print('Pandas ver.', pd.__version__)

Pandas ver. 0.23.4


In [4]:
def sparql_service_to_dataframe(service, query):
    """
    Helper function to convert SPARQL results into a Pandas DataFrame.
    
    Credit to Ted Lawless https://lawlesst.github.io/notebook/sparql-dataframe.html
    """
    sparql = SPARQLWrapper(service)
    sparql.setQuery(query)
    sparql.setReturnFormat(JSON)
    result = sparql.query()

    processed_results = json.load(result.response)
    cols = processed_results['head']['vars']

    out = []
    for row in processed_results['results']['bindings']:
        item = []
        for c in cols:
            item.append(row.get(c, {}).get('value'))
        out.append(item)

    return pd.DataFrame(out, columns=cols)



## Run queries

In [5]:
wds_Corese = 'http://corese.inria.fr/sparql'

In [6]:
query = '''

select *
{
  ?x ?p ?y
}
limit 10
'''

In [7]:
df = sparql_service_to_dataframe(wds_Corese, query)
print(df.shape)

(10, 3)


In [9]:
pd.set_option('display.max_colwidth', -1) # if your Pandas version is < 1.0 then use -1 as second parameter, None otherwise
pd.set_option('display.precision', 3)
pd.set_option('display.max_rows', 999)

df.head(10)

x  \
0  http://www.inria.fr/2015/humans#Man          
1  http://www.inria.fr/2015/humans#Person       
2  http://www.inria.fr/2015/humans#Lecturer     
3  http://www.inria.fr/2015/humans#Researcher   
4  http://www.inria.fr/2015/humans#Woman        

                                         p  \
0  http://ns.inria.fr/sparql-template/icon   
1  http://ns.inria.fr/sparql-template/icon   
2  http://ns.inria.fr/sparql-template/icon   
3  http://ns.inria.fr/sparql-template/icon   
4  http://ns.inria.fr/sparql-template/icon   

                                          y  
0  http://corese.inria.fr/img/male.png       
1  http://corese.inria.fr/img/person.png     
2  http://corese.inria.fr/img/professor.jpg  
3  http://corese.inria.fr/img/professor.jpg  
4  http://corese.inria.fr/img/female.png